# Hiteligénylők adatainak elemzése

In [ ]:
import numpy as np
import pandas as pd
from matplotlib import pyplot

%matplotlib inline

In [ ]:
df = pd.read_csv("bankloan.csv")

In [ ]:
df.dropna(axis=0, inplace=True)

In [ ]:
df

## 1 - Dimenziócsökkentés PCA-val

In [ ]:
from sklearn.decomposition import PCA

### 1.1 - PCA adatelőkészítés nélkül

In [ ]:
df_wo_target = df.iloc[:,:-1]
pca = PCA(n_components=0.7, random_state=0)
pca.fit(df_wo_target)

In [ ]:
pca.explained_variance_ratio_

In [ ]:
pca.n_components_

In [ ]:
pca.components_.T

In [ ]:
df.var()

### 1.2 - PCA z-score normalizálás után

In [ ]:
df_standardized = (df_wo_target - df_wo_target.mean()) / df_wo_target.std()
print "Means:\n", df_standardized.mean()
print "\nVariances:\n", df_standardized.var()

In [ ]:
pca.fit(df_standardized)

In [ ]:
pca.explained_variance_ratio_

In [ ]:
pca.components_.T

### 1.3 - Komponens mátrix értelmezése (forgatás segítségével)

In [ ]:
from fa_kit.rotation import VarimaxRotatorPython

In [ ]:
varimax = VarimaxRotatorPython()

In [ ]:
rotated_weights = varimax.rotate(pca.components_.T)

In [ ]:
rotated_weights

In [ ]:
# 1. komponens: {"age", "employ", "address", "income"} : Anyagi biztonság (a bank számára kockázatmentesség)
# 2. komponens: {"debtinc", "creddebt", "othdebt"}     : Hitelállomány, eladósodottság (a bank számára kockázatosság)
# 3. komponens: {"ed"}                                 : Végzettség

### 1.4 - Az alacsonyabb dimenziós reprezentáció vizsgálata

In [ ]:
# transzformáljuk az eredeti adatsorunkat 3 dimenziósra
df_lowdim = pd.DataFrame(np.dot(df_standardized, rotated_weights), columns=["security", "debt", "education"])

In [ ]:
# csatoljuk vissza hozzá a célváltozót
df_lowdim["default"] = df["default"]

In [ ]:
df_lowdim

In [ ]:
# nézzük meg, hogy az első két főkomponens mennyire segíti a döntésünket (lila: törlesztett, sárga: bebukott hiteles ügyfél)
pyplot.scatter(df_lowdim["security"], df_lowdim["debt"], c=df_lowdim["default"])
pyplot.xlabel("Anyagi biztonsag")
pyplot.ylabel("Tartozas merteke")

## 2 - Klaszterezés (k-means)

In [ ]:
from sklearn.cluster import k_means

In [ ]:
# a célváltozót kihagyva keressünk 2 klasztert (az összes cpu magot használva)
centroids, labels, _ = k_means(df_lowdim.iloc[:,:-1], 2, n_jobs=-1)

In [ ]:
# mentsük el a dataframe-be a kalszterezés által adott címkéket
df_lowdim["cluster_label"] = labels

In [ ]:
# nézzük meg, hogy a klaszterezéssel mennyire sikerült volna a célváltozó struktúráját megtalálni
tab = pd.crosstab(df_lowdim["cluster_label"], df_lowdim["default"])

In [ ]:
tab

In [ ]:
tab / tab.sum()

In [ ]:
# a klaszterezés elég rosszul találta el az eredeti címkéket: a ténylegesen be nem csődöltek 71%-át ugyan egy csoportba rakta,
# azonban a becsődöltek 73%-át is hozzájuk vette - nézzük meg mi lehet az oka!

In [ ]:
# klaszter középpontok
print centroids

In [ ]:
df_lowdim.hist()

In [ ]:
# az első klaszter tehát az alacsony anyagi biztonságú, alacsony hitelű, alacsony végzettségű emberek;
# a második klaszter a magasabb anyagi biztonságú, magasabb hitelű, magasabb végzettségű emberek;
# ezek alapján nem is csoda, hogy a klaszterek nem jól írták le, hogy a csoportra mennyire jellemző a hitel bebukás

## 3 - Ensemble módszerek: random forest

In [ ]:
from sklearn.ensemble import RandomForestClassifier

### 3.1 - Dimenziócsökkentés előtt

In [ ]:
# bontsuk az adatot tanító és teszt halmazra; az utolsó 150 adat legyen a tanító halmaz
train = df.iloc[:-150, :]
test = df.iloc[-150:, :]

In [ ]:
# építsünk random forest ensemble-t, amiben 15 véletlenített döntési fa legyen (az összes CPU magot használva)
rfc = RandomForestClassifier(n_estimators=15, n_jobs=-1)

In [ ]:
# első paraméter az összes oszlop kivéve a célváltozót, a második a célváltozó
rfc.fit(train.iloc[:, :-1], train.iloc[:, -1])

In [ ]:
# teszt halmazon lefuttatjuk
predicted_labels = rfc.predict(test.iloc[:, :-1])

In [ ]:
# kereszttáblával megvizsgáljuk mennyiből mennyit talált elt
tab = pd.crosstab(predicted_labels, test.iloc[:, -1])

In [ ]:
tab / tab.sum()

In [ ]:
# a be nem csődölők 94%-át eltalálta, a becsődölőknek pedig a 42%-át

### 3.2 - Dimenziócsökkentés után

In [ ]:
# bontsuk az adatot tanító és teszt halmazra; az utolsó 150 adat legyen a tanító halmaz
train = df_lowdim.iloc[:-150, :]
test = df_lowdim.iloc[-150:, :]

In [ ]:
# építsünk random forest ensemble-t, amiben 15 véletlenített döntési fa legyen (az összes CPU magot használva)
rfc = RandomForestClassifier(n_estimators=15, n_jobs=-1)

In [ ]:
# első paraméter a 3 főkomponens, második a célváltozó
rfc.fit(train.iloc[:, :3], train.iloc[:, 3])

In [ ]:
# teszt halmazon lefuttatjuk
predicted_labels = rfc.predict(test.iloc[:, :3])

In [ ]:
# kereszttáblával megvizsgáljuk mennyiből mennyit talált elt
tab = pd.crosstab(predicted_labels, test.iloc[:, 3])

In [ ]:
tab / tab.sum()

In [ ]:
# A be nem csődölők 88%-át eltalálta, a becsődölőknek pedig a 33%-át.
# Láthatjuk, hogy a dimenziócsökkentés során veszített információ (ahogy azt várnánk) rontja kicsit az eredményt.
# Ugyanakkor 8 változó helyett csak 3 változót használtunk (az adat több mint felét kidobtuk), mégis az információ ~25%-át
# vesztettük csak el, a modellünk előrejelző ereje pedig "csak" ~8%-kal romlott